In [17]:
import pandas as pd
import geopandas as gpd
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import sqlite3
import tempfile
import warnings
from pathlib import Path
from shapely import wkt, wkb
import networkx as nx
from collections import Counter
import binascii

warnings.filterwarnings('ignore')
plt.style.use('default')

In [18]:
def decode_hex_geometry(hex_str):
    """
    Decode hex-encoded WKB geometry to Shapely geometry object.
    """
    try:
        if hex_str is None:
            return None
        
        # Remove any quotes if present and clean the string
        hex_str = str(hex_str).strip("'").strip('"').strip()
        
        # Debug: print first few characters to see what we're working with
        if len(hex_str) > 20:
            print(f"Debug - First 20 chars of hex: {hex_str[:20]}")
        else:
            print(f"Debug - Full hex string: {hex_str}")
        
        # Check if it's a valid hex string
        if not hex_str or len(hex_str) % 2 != 0:
            print(f"Invalid hex string length: {len(hex_str)}")
            return None
            
        # Convert hex to binary
        binary = binascii.unhexlify(hex_str)
        # Convert binary to Shapely geometry
        geom = wkb.loads(binary)
        print(f"Successfully decoded geometry: {type(geom)}")
        return geom
        
    except Exception as e:
        print(f"Error decoding geometry '{hex_str[:50] if hex_str else 'None'}...': {e}")
        return None

def parse_sql_file(sql_file_path):
    """
    Parse SQL file and extract ALL INSERT statements into a GeoDataFrame.
    Handles both old osm2po format (multiple INSERT blocks) and new Python format.
    Returns a GeoPandas DataFrame with proper geometry objects.
    """
    print(f"Parsing: {sql_file_path}")
    
    with open(sql_file_path, 'r', encoding='utf-8') as f:
        content = f.read()
    
    # Find ALL INSERT statements
    all_insert_positions = []
    start_pos = 0
    while True:
        insert_pos = content.find("INSERT INTO public_2po_4pgr", start_pos)
        if insert_pos == -1:
            break
        all_insert_positions.append(insert_pos)
        start_pos = insert_pos + 1
    
    if not all_insert_positions:
        print("No INSERT statements found")
        return None
    
    print(f"Found {len(all_insert_positions)} INSERT statement(s)")
    
    # Process each INSERT statement
    all_rows = []
    
    for i, insert_start in enumerate(all_insert_positions):
        print(f"Processing INSERT statement {i+1}/{len(all_insert_positions)}")
        
        # Find VALUES section for this INSERT
        values_start = content.find("VALUES", insert_start)
        if values_start == -1:
            print(f"No VALUES section found in INSERT {i+1}")
            continue
        
        # Check format for first INSERT only
        if i == 0:
            insert_line = content[insert_start:values_start]
            has_column_names = "(" in insert_line and "osm_id" in insert_line
            print(f"Format detected: {'New (with column names)' if has_column_names else 'Old (VALUES only)'}")
        
        # Find the end of this INSERT statement
        # Look for the next INSERT or end of file
        if i < len(all_insert_positions) - 1:
            next_insert = all_insert_positions[i + 1]
            values_section = content[values_start + 6:next_insert]
        else:
            values_section = content[values_start + 6:]
        
        # Find the semicolon that ends this INSERT
        semicolon_pos = values_section.find(';')
        if semicolon_pos != -1:
            values_section = values_section[:semicolon_pos]
        
        # Parse individual value tuples for this INSERT
        insert_rows = parse_values_section(values_section, has_column_names)
        all_rows.extend(insert_rows)
        print(f"  Parsed {len(insert_rows)} rows from INSERT {i+1}")
    
    if not all_rows:
        print("No valid rows parsed from any INSERT statement")
        return None
    
    # Create DataFrame with consistent column names
    columns = ['osm_id', 'osm_name', 'osm_meta', 'osm_source_id', 'osm_target_id', 
               'clazz', 'flags', 'source', 'target', 'km', 'kmh', 'cost', 
               'reverse_cost', 'x1', 'y1', 'x2', 'y2', 'geom_way']
    
    df = pd.DataFrame(all_rows, columns=columns)
    print(f"Total parsed: {len(df)} rows from {len(all_insert_positions)} INSERT statements")
    
    # Convert hex-encoded geometries to Shapely objects
    print("Converting geometries...")
    print(f"Sample geom_way values:")
    print(f"  First 3 values: {df['geom_way'].head(3).tolist()}")
    print(f"  Data types: {df['geom_way'].dtype}")
    print(f"  Null values: {df['geom_way'].isnull().sum()}")
    
    # Only process first few rows for debugging
    print("Processing first 3 geometries for debugging...")
    df['geometry'] = df['geom_way'].apply(decode_hex_geometry)
    
    # Create GeoDataFrame
    gdf = gpd.GeoDataFrame(df, geometry='geometry', crs="EPSG:4326")
    
    # Drop the original geom_way column as it's no longer needed
    gdf = gdf.drop(columns=['geom_way'])
    
    print("Successfully created GeoDataFrame")
    return gdf

def parse_values_section(values_section, has_column_names=True):
    """
    Parse the VALUES section of an INSERT statement.
    """
    rows = []
    current_row = ""
    paren_count = 0
    in_string = False
    escape_next = False
    
    for char in values_section:
        if escape_next:
            current_row += char
            escape_next = False
            continue
            
        if char == '\\' and in_string:
            escape_next = True
            current_row += char
            continue
            
        if char == "'" and not escape_next:
            in_string = not in_string
            
        if not in_string:
            if char == '(':
                if paren_count == 0:
                    current_row = ""
                paren_count += 1
            elif char == ')':
                paren_count -= 1
                if paren_count == 0:
                    # Complete row found
                    row_data = parse_row_values(current_row, has_column_names)
                    if row_data:
                        rows.append(row_data)
                    continue
                    
        current_row += char
    
    return rows

def parse_row_values(row_str, has_column_names=True):
    """
    Parse individual row values from SQL INSERT statement.
    
    Args:
        row_str: The values part of the INSERT statement
        has_column_names: If False, expects old format with id column first
    """
    try:
        values = []
        current_value = ""
        in_string = False
        escape_next = False
        
        for char in row_str:
            if escape_next:
                current_value += char
                escape_next = False
                continue
                
            if char == '\\' and in_string:
                escape_next = True
                current_value += char
                continue
                
            if char == "'" and not escape_next:
                in_string = not in_string
                if not in_string:
                    # End of string value
                    values.append(current_value)
                    current_value = ""
                continue
            elif in_string:
                current_value += char
                continue
            elif char == ',':
                if current_value.strip():
                    val = current_value.strip()
                    values.append(convert_value(val))
                current_value = ""
            else:
                current_value += char
        
        # Handle last value
        if current_value.strip():
            val = current_value.strip()
            values.append(convert_value(val))
        
        # Handle different formats
        if not has_column_names:
            # Old format: id, osm_id, osm_name, osm_meta, osm_source_id, osm_target_id, 
            #            clazz, flags, source, target, km, kmh, cost, reverse_cost, 
            #            x1, y1, x2, y2, geom_way
            if len(values) == 19:  # Expected length for old format
                # Skip the id column (first value) and return the rest
                return values[1:]  # Skip id, return osm_id onwards
            else:
                print(f"Unexpected number of values in old format: {len(values)} (expected 19)")
                return None
        else:
            # New format: osm_id, osm_name, osm_meta, osm_source_id, osm_target_id,
            #            clazz, flags, source, target, km, kmh, cost, reverse_cost,
            #            x1, y1, x2, y2, geom_way
            expected_length = 18
            if len(values) == expected_length:
                return values
            else:
                # Debug: print the actual values to see what's wrong
                print(f"Unexpected number of values in new format: {len(values)} (expected {expected_length})")
                if len(values) <= 5:  # Only print if it's a reasonable number to debug
                    print(f"Values: {values}")
                return None
        
    except Exception as e:
        print(f"Error parsing row: {e}")
        return None

def convert_value(val_str):
    """Convert a string value to appropriate Python type."""
    val = val_str.strip()
    
    if val.upper() == 'NULL':
        return None
    elif val == 'inf':
        return float('inf')
    elif val == '1000000.0':  # Handle old format large reverse costs
        return float('inf')
    elif val.startswith("'") and val.endswith("'"):
        return val[1:-1]  # Remove quotes
    else:
        try:
            # Try to convert to appropriate type
            if '.' in val or 'E-' in val.upper() or 'E+' in val.upper():
                return float(val)
            else:
                return int(val)
        except ValueError:
            return val

In [19]:
# File paths
old_sql = "/Users/magic-rabbit/Documents/00_Tech-Repositories/05_MASTER_THESIS/gridtracer/gridtracer/data/output/CA/Alameda_County/STREET_NETWORK/old_routing_network.sql"
new_sql = "/Users/magic-rabbit/Documents/00_Tech-Repositories/05_MASTER_THESIS/gridtracer/gridtracer/data/output/CA/Alameda_County/STREET_NETWORK/new_routing_network.sql"
# Parse both files
print("Loading Old OSM2PO data...")
old_df = parse_sql_file(old_sql)

print("\nLoading New Python implementation data...")
new_df = parse_sql_file(new_sql)

# Basic statistics
print("\n" + "="*50)
print("BASIC COMPARISON")
print("="*50)
print(f"Old OSM2PO records: {len(old_df) if old_df is not None else 0}")
print(f"New Python records: {len(new_df) if new_df is not None else 0}")

if old_df is not None and new_df is not None:
    diff = len(new_df) - len(old_df)
    pct_diff = (diff / len(old_df)) * 100
    print(f"Difference: {diff:+d} records ({pct_diff:+.2f}%)")

Loading Old OSM2PO data...
Parsing: /Users/magic-rabbit/Documents/00_Tech-Repositories/05_MASTER_THESIS/gridtracer/gridtracer/data/output/CA/Alameda_County/STREET_NETWORK/old_routing_network.sql
Found 627 INSERT statement(s)
Processing INSERT statement 1/627
Format detected: Old (VALUES only)
  Parsed 25 rows from INSERT 1
Processing INSERT statement 2/627
Unexpected number of values in old format: 20 (expected 19)
  Parsed 24 rows from INSERT 2
Processing INSERT statement 3/627
  Parsed 25 rows from INSERT 3
Processing INSERT statement 4/627
  Parsed 25 rows from INSERT 4
Processing INSERT statement 5/627
Unexpected number of values in old format: 20 (expected 19)
Unexpected number of values in old format: 20 (expected 19)
Unexpected number of values in old format: 20 (expected 19)
Unexpected number of values in old format: 20 (expected 19)
Unexpected number of values in old format: 20 (expected 19)
Unexpected number of values in old format: 20 (expected 19)
Unexpected number of value

In [20]:
def analyze_data_quality(df, name):
    """Analyze data quality metrics for a dataset."""
    print(f"\n{name} DATA QUALITY ANALYSIS")
    print("="*50)
    
    # Missing values
    missing = df.isnull().sum()
    print("Missing values:")
    for col, count in missing.items():
        if count > 0:
            pct = (count / len(df)) * 100
            print(f"  {col}: {count} ({pct:.1f}%)")
    
    # Infinite values in cost columns
    inf_cost = (df['cost'] == float('inf')).sum()
    inf_reverse = (df['reverse_cost'] == float('inf')).sum()
    print(f"\nInfinite costs: {inf_cost} ({(inf_cost/len(df)*100):.1f}%)")
    print(f"Infinite reverse costs: {inf_reverse} ({(inf_reverse/len(df)*100):.1f}%)")
    
    # Zero length edges
    zero_km = (df['km'] == 0).sum()
    print(f"Zero length edges: {zero_km} ({(zero_km/len(df)*100):.1f}%)")
    
    # Speed distribution
    print(f"\nSpeed (kmh) distribution:")
    print(f"  Min: {df['kmh'].min()}")
    print(f"  Max: {df['kmh'].max()}")
    print(f"  Mean: {df['kmh'].mean():.1f}")
    print(f"  Zero speed: {(df['kmh'] == 0).sum()} ({(df['kmh'] == 0).sum()/len(df)*100:.1f}%)")
    
    return {
        'total_records': len(df),
        'missing_values': missing.sum(),
        'inf_costs': inf_cost,
        'zero_length': zero_km,
        'avg_speed': df['kmh'].mean()
    }

# Analyze both datasets
if old_df is not None:
    old_quality = analyze_data_quality(old_df, "OLD OSM2PO")

if new_df is not None:
    new_quality = analyze_data_quality(new_df, "NEW PYTHON")


OLD OSM2PO DATA QUALITY ANALYSIS
Missing values:
  osm_name: 10266 (68.0%)
  osm_meta: 15107 (100.0%)

Infinite costs: 0 (0.0%)
Infinite reverse costs: 2444 (16.2%)
Zero length edges: 0 (0.0%)

Speed (kmh) distribution:
  Min: 5
  Max: 90
  Mean: 19.1
  Zero speed: 0 (0.0%)

NEW PYTHON DATA QUALITY ANALYSIS
Missing values:
  osm_name: 14424 (67.7%)
  osm_meta: 21294 (100.0%)

Infinite costs: 0 (0.0%)
Infinite reverse costs: 3062 (14.4%)
Zero length edges: 0 (0.0%)

Speed (kmh) distribution:
  Min: 5
  Max: 90
  Mean: 22.9
  Zero speed: 0 (0.0%)


In [21]:
def spatial_analysis(df, name):
    """Perform spatial analysis on the dataset."""
    print(f"\n{name} SPATIAL ANALYSIS")
    print("="*50)
    
    # Bounding box
    print("Bounding box:")
    print(f"  X: {df['x1'].min():.6f} to {df['x1'].max():.6f}")
    print(f"  Y: {df['y1'].min():.6f} to {df['y1'].max():.6f}")
    
    # Edge length statistics
    print(f"\nEdge lengths (km):")
    print(f"  Min: {df['km'].min():.6f}")
    print(f"  Max: {df['km'].max():.6f}")
    print(f"  Mean: {df['km'].mean():.6f}")
    print(f"  Median: {df['km'].median():.6f}")
    print(f"  Total: {df['km'].sum():.2f} km")
    
    # Length distribution percentiles
    percentiles = [25, 50, 75, 90, 95, 99]
    print(f"\nLength percentiles (km):")
    for p in percentiles:
        val = np.percentile(df['km'], p)
        print(f"  {p}th: {val:.6f}")

if old_df is not None:
    spatial_analysis(old_df, "OLD OSM2PO")

if new_df is not None:
    spatial_analysis(new_df, "NEW PYTHON")


OLD OSM2PO SPATIAL ANALYSIS
Bounding box:
  X: 1.400119 to 1.789316
  Y: 42.424006 to 42.658071

Edge lengths (km):
  Min: 0.000315
  Max: 5.934682
  Mean: 0.134799
  Median: 0.037855
  Total: 2036.42 km

Length percentiles (km):
  25th: 0.011345
  50th: 0.037855
  75th: 0.118274
  90th: 0.332309
  95th: 0.588202
  99th: 1.505216

NEW PYTHON SPATIAL ANALYSIS
Bounding box:
  X: 1.400119 to 1.783545
  Y: 42.418259 to 42.676170

Edge lengths (km):
  Min: 0.000499
  Max: 7.578810
  Mean: 0.177931
  Median: 0.054810
  Total: 3788.87 km

Length percentiles (km):
  25th: 0.017797
  50th: 0.054810
  75th: 0.163113
  90th: 0.442195
  95th: 0.778423
  99th: 1.847980


: 

In [ ]:
def analyze_road_classification(df, name):
    """Analyze road classification and attributes."""
    print(f"\n{name} ROAD CLASSIFICATION")
    print("="*50)
    
    # Class distribution
    class_dist = df['clazz'].value_counts().sort_index()
    print("Class distribution:")
    for clazz, count in class_dist.items():
        pct = (count / len(df)) * 100
        print(f"  Class {clazz}: {count} ({pct:.1f}%)")
    
    # Speed by class
    print(f"\nAverage speed by class:")
    speed_by_class = df.groupby('clazz')['kmh'].agg(['mean', 'count'])
    for clazz, row in speed_by_class.iterrows():
        print(f"  Class {clazz}: {row['mean']:.1f} kmh (n={row['count']})")
    
    # Flags distribution
    print(f"\nFlags distribution:")
    flag_dist = df['flags'].value_counts().sort_index()
    for flag, count in flag_dist.head(10).items():
        pct = (count / len(df)) * 100
        print(f"  Flag {flag}: {count} ({pct:.1f}%)")

if old_df is not None:
    analyze_road_classification(old_df, "OLD OSM2PO")

if new_df is not None:
    analyze_road_classification(new_df, "NEW PYTHON")

In [10]:
def analyze_graph_connectivity(df, name):
    """Analyze graph connectivity and routing properties."""
    print(f"\n{name} GRAPH CONNECTIVITY")
    print("="*50)
    
    # Create networkx graph
    G = nx.DiGraph()
    
    # Add edges
    for _, row in df.iterrows():
        source = row['source']
        target = row['target']

In [ ]:
def analyze_duplicates(df, name):
    """Analyze duplicate records in the dataset."""
    print(f"\n{name} DUPLICATE ANALYSIS")
    print("="*50)
    
    # Check for duplicate OSM IDs
    duplicate_osm_ids = df[df.duplicated(subset=['osm_id'], keep=False)]
    unique_duplicates = df['osm_id'].duplicated().sum()
    
    print(f"Duplicate OSM IDs: {unique_duplicates}")
    if unique_duplicates > 0:
        print(f"Total records with duplicate OSM IDs: {len(duplicate_osm_ids)}")
        
        # Show examples of duplicates
        print(f"\nFirst 5 duplicate OSM ID examples:")
        dup_ids = df[df['osm_id'].duplicated(keep=False)]['osm_id'].value_counts().head()
        for osm_id, count in dup_ids.items():
            print(f"  OSM ID {osm_id}: {count} occurrences")
            
        # Show details for first duplicate
        if len(dup_ids) > 0:
            first_dup_id = dup_ids.index[0]
            dup_records = df[df['osm_id'] == first_dup_id][['osm_id', 'source', 'target', 'km', 'clazz', 'kmh']]
            print(f"\nDetails for OSM ID {first_dup_id}:")
            print(dup_records.to_string())
    
    # Check for exact duplicate rows (all columns)
    exact_duplicates = df.duplicated().sum()
    print(f"\nExact duplicate rows: {exact_duplicates}")
    
    # Check for duplicate source-target pairs
    duplicate_edges = df.duplicated(subset=['source', 'target']).sum()
    print(f"Duplicate source-target pairs: {duplicate_edges}")
    
    # Check for self-loops
    self_loops = (df['source'] == df['target']).sum()
    print(f"Self-loops (source == target): {self_loops}")
    
    return {
        'duplicate_osm_ids': unique_duplicates,
        'exact_duplicates': exact_duplicates,
        'duplicate_edges': duplicate_edges,
        'self_loops': self_loops
    }

# Analyze duplicates in both datasets
if old_df is not None:
    old_dup_stats = analyze_duplicates(old_df, "OLD OSM2PO")

if new_df is not None:
    new_dup_stats = analyze_duplicates(new_df, "NEW PYTHON")

In [ ]:
def compare_osm_ids(old_df, new_df):
    """Compare OSM IDs between old and new datasets to find missing segments."""
    print("\nOSM ID COMPARISON ANALYSIS")
    print("="*50)
    
    # Get unique OSM IDs from both datasets
    old_osm_ids = set(old_df['osm_id'].unique())
    new_osm_ids = set(new_df['osm_id'].unique())
    
    # Find missing and extra segments
    missing_in_new = old_osm_ids - new_osm_ids
    extra_in_new = new_osm_ids - old_osm_ids
    common_osm_ids = old_osm_ids & new_osm_ids
    
    print(f"OSM IDs in old dataset: {len(old_osm_ids):,}")
    print(f"OSM IDs in new dataset: {len(new_osm_ids):,}")
    print(f"Common OSM IDs: {len(common_osm_ids):,}")
    print(f"Missing in new (lost segments): {len(missing_in_new):,}")
    print(f"Extra in new (new segments): {len(extra_in_new):,}")
    
    # Calculate percentages
    if len(old_osm_ids) > 0:
        missing_pct = (len(missing_in_new) / len(old_osm_ids)) * 100
        print(f"Missing percentage: {missing_pct:.2f}%")
    
    if len(new_osm_ids) > 0:
        extra_pct = (len(extra_in_new) / len(new_osm_ids)) * 100
        print(f"Extra percentage: {extra_pct:.2f}%")
    
    # Show examples of missing segments
    if missing_in_new:
        print(f"\nFirst 10 missing OSM IDs (in old but not new):")
        missing_sample = list(missing_in_new)[:10]
        for osm_id in missing_sample:
            old_record = old_df[old_df['osm_id'] == osm_id].iloc[0]
            print(f"  OSM ID {osm_id}: {old_record['osm_name']} (class: {old_record['clazz']}, km: {old_record['km']:.4f})")
    
    # Show examples of extra segments  
    if extra_in_new:
        print(f"\nFirst 10 extra OSM IDs (in new but not old):")
        extra_sample = list(extra_in_new)[:10]
        for osm_id in extra_sample:
            new_record = new_df[new_df['osm_id'] == osm_id].iloc[0]
            print(f"  OSM ID {osm_id}: {new_record['osm_name']} (class: {new_record['clazz']}, km: {new_record['km']:.4f})")
    
    return {
        'common_ids': common_osm_ids,
        'missing_in_new': missing_in_new,
        'extra_in_new': extra_in_new,
        'missing_count': len(missing_in_new),
        'extra_count': len(extra_in_new),
        'common_count': len(common_osm_ids)
    }

# Compare OSM IDs if both datasets exist
if old_df is not None and new_df is not None:
    comparison_stats = compare_osm_ids(old_df, new_df)

In [13]:
def compare_matching_segments(old_df, new_df, common_ids):
    """Compare attributes of segments that exist in both datasets."""
    print("\nMATCHING SEGMENTS COMPARISON")
    print("="*50)
    
    # Filter to common OSM IDs only
    old_common = old_df[old_df['osm_id'].isin(common_ids)].set_index('osm_id').sort_index()
    new_common = new_df[new_df['osm_id'].isin(common_ids)].set_index('osm_id').sort_index()
    
    print(f"Comparing {len(common_ids):,} matching segments...")
    
    # Compare key attributes
    attributes_to_compare = ['km', 'kmh', 'cost', 'reverse_cost', 'clazz', 'flags']
    differences = {}
    
    for attr in attributes_to_compare:
        if attr in old_common.columns and attr in new_common.columns:
            # Handle infinite values for comparison
            old_vals = old_common[attr].replace([np.inf, -np.inf], np.nan)
            new_vals = new_common[attr].replace([np.inf, -np.inf], np.nan)
            
            # Count differences
            if attr in ['km', 'cost', 'reverse_cost']:
                # For continuous values, use tolerance
                tolerance = 1e-6
                diff_mask = np.abs(old_vals - new_vals) > tolerance
            else:
                # For discrete values, exact comparison
                diff_mask = old_vals != new_vals
            
            # Remove NaN comparisons
            valid_mask = ~(old_vals.isna() | new_vals.isna())
            diff_count = (diff_mask & valid_mask).sum()
            total_valid = valid_mask.sum()
            
            differences[attr] = {
                'different_count': diff_count,
                'total_compared': total_valid,
                'percentage': (diff_count / total_valid * 100) if total_valid > 0 else 0
            }
            
            print(f"\n{attr.upper()} comparison:")
            print(f"  Different: {diff_count:,} / {total_valid:,} ({differences[attr]['percentage']:.2f}%)")
            
            if diff_count > 0 and diff_count <= 10:
                # Show examples of differences for small counts
                diff_indices = old_common.index[diff_mask & valid_mask]
                print(f"  Examples of differences:")
                for idx in diff_indices[:5]:
                    old_val = old_vals.loc[idx]
                    new_val = new_vals.loc[idx]
                    if attr in ['km', 'cost', 'reverse_cost']:
                        print(f"    OSM ID {idx}: {old_val:.6f} -> {new_val:.6f}")
                    else:
                        print(f"    OSM ID {idx}: {old_val} -> {new_val}")
    
    return differences

# Compare matching segments if we have common IDs
if old_df is not None and new_df is not None and 'comparison_stats' in locals():
    if comparison_stats['common_count'] > 0:
        segment_differences = compare_matching_segments(
            old_df, new_df, comparison_stats['common_ids']
        )

In [ ]:
def analyze_missing_by_road_type(old_df, missing_ids, extra_ids):
    """Analyze missing and extra segments by road classification."""
    print("\nMISSING SEGMENTS BY ROAD TYPE")
    print("="*50)
    
    if missing_ids:
        missing_segments = old_df[old_df['osm_id'].isin(missing_ids)]
        print(f"Missing segments analysis ({len(missing_segments)} total):")
        
        # By class
        missing_by_class = missing_segments['clazz'].value_counts().sort_index()
        for clazz, count in missing_by_class.items():
            total_class = (old_df['clazz'] == clazz).sum()
            pct_missing = (count / total_class * 100) if total_class > 0 else 0
            print(f"  Class {clazz}: {count} missing / {total_class} total ({pct_missing:.1f}%)")
        
        # By speed
        print(f"\nMissing segments by speed:")
        missing_by_speed = missing_segments['kmh'].value_counts().sort_index()
        for speed, count in missing_by_speed.head(10).items():
            print(f"  {speed} kmh: {count} segments")
        
        # By length
        print(f"\nMissing segments length statistics:")
        print(f"  Total missing length: {missing_segments['km'].sum():.2f} km")
        print(f"  Average missing length: {missing_segments['km'].mean():.4f} km")
        print(f"  Max missing length: {missing_segments['km'].max():.4f} km")
    
    if extra_ids and new_df is not None:
        extra_segments = new_df[new_df['osm_id'].isin(extra_ids)]
        print(f"\nEXTRA SEGMENTS ANALYSIS ({len(extra_segments)} total):")
        
        # By class
        extra_by_class = extra_segments['clazz'].value_counts().sort_index()
        for clazz, count in extra_by_class.items():
            print(f"  Class {clazz}: {count} extra segments")
        
        # Total extra length
        print(f"\nExtra segments total length: {extra_segments['km'].sum():.2f} km")

# Analyze missing segments by type
if old_df is not None and new_df is not None and 'comparison_stats' in locals():
    analyze_missing_by_road_type(
        old_df, 
        comparison_stats['missing_in_new'], 
        comparison_stats['extra_in_new']
    )

In [ ]:
def generate_validation_summary():
    """Generate a comprehensive validation summary."""
    print("\n" + "="*70)
    print("VALIDATION SUMMARY REPORT")
    print("="*70)
    
    # Data completeness
    if old_df is not None and new_df is not None:
        print(f"📊 DATA COMPLETENESS:")
        print(f"   Old implementation: {len(old_df):,} segments")
        print(f"   New implementation: {len(new_df):,} segments")
        
        if 'comparison_stats' in locals():
            print(f"   Common segments: {comparison_stats['common_count']:,}")
            print(f"   Missing segments: {comparison_stats['missing_count']:,}")
            print(f"   Extra segments: {comparison_stats['extra_count']:,}")
            
            # Calculate success rate
            success_rate = (comparison_stats['common_count'] / len(old_df)) * 100
            print(f"   Migration success rate: {success_rate:.1f}%")
    
    # Data quality issues
    print(f"\n🔍 DATA QUALITY:")
    if 'old_dup_stats' in locals():
        print(f"   Old duplicates: {old_dup_stats['duplicate_osm_ids']} OSM IDs")
    if 'new_dup_stats' in locals():
        print(f"   New duplicates: {new_dup_stats['duplicate_osm_ids']} OSM IDs")
    
    # Critical issues to investigate
    print(f"\n⚠️  CRITICAL ISSUES TO INVESTIGATE:")
    issues = []
    
    if 'comparison_stats' in locals():
        if comparison_stats['missing_count'] > len(old_df) * 0.05:  # >5% missing
            issues.append(f"High number of missing segments ({comparison_stats['missing_count']:,})")
        
        if comparison_stats['extra_count'] > len(old_df) * 0.05:  # >5% extra
            issues.append(f"High number of extra segments ({comparison_stats['extra_count']:,})")
    
    if 'new_dup_stats' in locals() and new_dup_stats['duplicate_osm_ids'] > 0:
        issues.append(f"Duplicate OSM IDs in new implementation")
    
    if not issues:
        print("   ✅ No critical issues detected!")
    else:
        for i, issue in enumerate(issues, 1):
            print(f"   {i}. {issue}")
    
    # Recommendations
    print(f"\n💡 RECOMMENDATIONS:")
    print(f"   1. Investigate missing segments by road classification")
    print(f"   2. Validate routing connectivity on sample routes") 
    print(f"   3. Performance test both implementations")
    print(f"   4. Check coordinate precision and projection accuracy")
    print(f"   5. Validate OSM tag interpretation consistency")

# Generate final summary
generate_validation_summary()